In [ ]:
!pip install transformers

In [10]:
import pandas as pd
import numpy as np
from transformers import BertTokenizer
from transformers import BertForSequenceClassification
from torch.utils.data import TensorDataset
from torch.utils.data import DataLoader, RandomSampler, SequentialSampler
from transformers import AdamW, get_linear_schedule_with_warmup
import torch
from tqdm import tqdm
import random
import numpy as np
from sklearn.metrics import f1_score
from sklearn.metrics import accuracy_score
import re
seed_val = 17
random.seed(seed_val)
np.random.seed(seed_val)
torch.manual_seed(seed_val)
torch.cuda.manual_seed_all(seed_val)

In [ ]:
## Reading the full data
full_train_data = pd.read_csv("/content/training.1600000.processed.noemoticon.csv",encoding='latin-1')

In [2]:
# Reading full test data
full_test_data = pd.read_csv('full_testing_data.csv')

In [34]:
## Defining the preprocessing function removing twitter handles ,  website links , digits and double spacing
def preprocessing(tweet):
  temp = tweet.lower()
  temp = re.sub('(@[A-Za-z]+[A-Za-z0-9-_]+)', ' ', temp)
  temp = re.sub(r'https\S+', '', temp)
  temp = re.sub(r'http\S+', '', temp)
  temp = re.sub(r'www\S+', '', temp)
#   temp = re.sub(r"([^ ]+(?<=\.[a-z]{3}))", " ", temp)
  temp = re.sub("[0-9]", " ", temp)
  temp = re.sub("\s\s+", " ", temp)
  return temp

In [14]:
full_test_data.iloc[5,:].tweet_text

'Milton on Bolton Wanderers 2 v 2 Leeds United, sat nav free night.: How Milton manages to write so much about su... http://t.co/MoIoMI4v'

In [4]:
full_test_data.shape

(28418, 4)

In [22]:
full_test_data.iloc[3,:].tweet_text

'Excuse the connectivity of this live stream, from Baba Amr, so many activists using only one Sat Modem. LIVE http://t.co/U283IhZ5 #Homs'

In [36]:
preprocessed_test_tweets = []
labels = []
for i in tqdm(range(full_test_data.shape[0])):
    row_val = full_test_data.iloc[i,:]
    if row_val.label == 1:
        continue
    tweet = preprocessing(row_val.tweet_text)
    preprocessed_test_tweets.append(tweet)
    if row_val.label == 2:
        labels.append(1)
    else:
        labels.append(0)

100%|██████████| 28418/28418 [00:03<00:00, 8207.29it/s]


In [51]:
test_info = {'Polarity':labels,'text':preprocessed_test_tweets}
full_test_data = pd.DataFrame(data=test_info)
full_test_data.to_csv("full_test_data.csv",index=True)

In [56]:
full_test_data.Polarity.value_counts()

1    10552
0     4356
Name: Polarity, dtype: int64

In [ ]:
columns = full_train_data.columns

In [ ]:
## renaming the columns
full_train_data.rename(columns={columns[0]: 'Polarity', columns[1]: 'tweetID', columns[2]:'date', columns[3]:'query', columns[4]:'user', columns[5]:'text'}, inplace=True)

In [ ]:
pre_processed_all_tweets = []
for tweet in tqdm(full_train_data.text):
  tweet = preprocessing(tweet)
  pre_processed_all_tweets.append(tweet)

In [ ]:
info = {'Polarity':full_train_data['Polarity'],'text':pre_processed_all_tweets}
full_training_data = pd.DataFrame(data = info)

In [ ]:
## Changing the polarity of the positive tweet to 1
full_training_data['Polarity'].mask(full_training_data['Polarity'] == 4, 1, inplace=True)

In [ ]:
## Writing to CSV file
full_training_data.to_csv("full_training_data.csv",index=True)

In [41]:
full_training_data = pd.read_csv('full_training_data.csv')

In [48]:
full_training_data.iloc[20,:].text

"one of my friend called me, and asked to meet with her at mid valley i've no time *sigh* "

In [11]:
X_training_data_full = full_training_data.text
Y_training_data_full = full_training_data.Polarity

In [57]:
X_testing_data = full_test_data.text
Y_testing_data = full_test_data.Polarity

In [58]:
# Using the BERT tokenizer to tokenize the values
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased',
                                         do_lower_case = True)

In [13]:
#encode train set
encoded_data_train = tokenizer.batch_encode_plus(X_training_data_full,
                                                add_special_tokens = True,
                                                return_attention_mask = True,
                                                pad_to_max_length = True,
                                                max_length = 256,
                                                return_tensors = 'pt')

Truncation was not explicitly activated but `max_length` is provided a specific value, please use `truncation=True` to explicitly truncate examples to max length. Defaulting to 'longest_first' truncation strategy. If you encode pairs of sequences (GLUE-style) with the tokenizer you can select this strategy more precisely by providing a specific strategy to `truncation`.
/usr4/cs505/orawal/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:2263: FutureWarning: The `pad_to_max_length` argument is deprecated and will be removed in a future version, use `padding=True` or `padding='longest'` to pad to the longest sequence in the batch, or use `padding='max_length'` to pad to a max length. In this case, you can give a specific length with `max_length` (e.g. `max_length=45`) or leave max_length to None to pad to the maximal input size of the model (e.g. 512 for Bert).
  warnings.warn(


In [60]:
#encode test set
encoded_data_test = tokenizer.batch_encode_plus(X_testing_data,
                                                add_special_tokens = True,
                                                return_attention_mask = True,
                                                pad_to_max_length = True,
                                                max_length = 256,
                                                return_tensors = 'pt')

In [14]:
#train set
input_ids_train = encoded_data_train['input_ids']
attention_masks_train = encoded_data_train['attention_mask']
labels_train = torch.tensor(Y_training_data_full)


In [61]:
#test set
input_ids_test = encoded_data_test['input_ids']
attention_masks_test = encoded_data_test['attention_mask']
labels_test = torch.tensor(Y_testing_data)

In [62]:
model = BertForSequenceClassification.from_pretrained('bert-base-uncased',
                                                      num_labels = 2,
                                                      output_attentions = False,
                                                      output_hidden_states = False)

Some weights of the model checkpoint at bert-base-uncased were not used when initializing BertForSequenceClassification: ['cls.seq_relationship.bias', 'cls.seq_relationship.weight', 'cls.predictions.transform.LayerNorm.weight', 'cls.predictions.decoder.weight', 'cls.predictions.transform.dense.bias', 'cls.predictions.transform.dense.weight', 'cls.predictions.transform.LayerNorm.bias', 'cls.predictions.bias']
- This IS expected if you are initializing BertForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertForSequenceClassification were not initialized from the model checkpoint at

In [16]:
#train set
dataset_train = TensorDataset(input_ids_train, 
                              attention_masks_train,
                              labels_train)

In [63]:
#test set
dataset_test = TensorDataset(input_ids_test, 
                              attention_masks_test,
                              labels_test)

In [17]:
validation_set_size = int(len(dataset_train)*0.2)
train_set_size = int(len(dataset_train) - validation_set_size)

In [18]:
validation_dataset,train_dataset = torch.utils.data.random_split(dataset_train, [validation_set_size, train_set_size], generator=torch.Generator().manual_seed(42))

In [15]:
import torch, gc
gc.collect()
torch.cuda.empty_cache()

In [19]:
device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")

In [20]:
torch.cuda.memory_allocated(device=device)

0

In [21]:
batch_size = 32
#train set
dataloader_train = DataLoader(train_dataset,
                              sampler = RandomSampler(train_dataset),
                              batch_size = batch_size)
dataloader_val = DataLoader(validation_dataset,sampler = RandomSampler(validation_dataset),
                              batch_size = batch_size)

In [64]:
#test set
batch_size = 32
dataloader_test = DataLoader(dataset_test,batch_size = batch_size,shuffle=True,drop_last=True)

In [22]:
optimizer = AdamW(model.parameters(),
                 lr = 1e-5,
                 eps = 1e-8) #2e-5 > 5e-5
                 
epochs = 10

scheduler = get_linear_schedule_with_warmup(optimizer,
                                           num_warmup_steps = 0,
                                           num_training_steps = len(dataloader_train)*epochs)


/usr4/cs505/orawal/.local/lib/python3.8/site-packages/transformers/optimization.py:306: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  warnings.warn(


In [23]:
label_dict = {'Negative' : 0 , 'Positive' : 1}

In [65]:
def evaluate(dataloader_val,model):

    model.cuda()
    #evaluation mode 
    model.eval()
    #tracking variables
    loss_val_total = 0
    predictions, true_vals = [], []
    
    for batch in tqdm(dataloader_val):
        
        #load into GPU
        batch = tuple(b.cuda() for b in batch)
        
        #define inputs
        inputs = {'input_ids':      batch[0],
                  'attention_mask': batch[1],
                  'labels':         batch[2]}

        #compute logits
        with torch.no_grad():        
            outputs = model(**inputs)
        
        #compute loss
        loss = outputs[0]
        logits = outputs[1]
        loss_val_total += loss.item()

        #compute accuracy
        logits = logits.detach().cpu().numpy()
        label_ids = inputs['labels'].cpu().numpy()
        predictions.append(logits)
        true_vals.append(label_ids)
    
    #compute average loss
    loss_val_avg = loss_val_total/len(dataloader_val) 
    
    predictions = np.concatenate(predictions, axis=0)
    true_vals = np.concatenate(true_vals, axis=0)
            
    return loss_val_avg, predictions, true_vals

In [66]:
def f1_score_func(preds, labels):
    preds_flat = np.argmax(preds, axis = 1).flatten()
    labels_flat = labels.flatten()
    return f1_score(labels_flat, preds, average = 'weighted')

In [67]:
def accuracy_per_class(preds, labels):
    label_dict = {'Negative' : 0 , 'Positive' : 1}
    label_dict_inverse = {v: k for k, v in label_dict.items()}
    
    #make prediction
    preds_flat = np.argmax(preds, axis=1).flatten()
    labels_flat = labels.flatten()
    
    for label in np.unique(labels_flat):
        y_preds = preds_flat[labels_flat==label]
        y_true = labels_flat[labels_flat==label]
        print(f'Class: {label_dict_inverse[label]}')
        print(f'Accuracy:{len(y_preds[y_preds==label])}/{len(y_true)}\n')
    
    print(f'Total accuracy is : {accuracy_score(labels_flat,preds_flat)}\n')
        
    

In [67]:
model = BertForSequenceClassification.from_pretrained('bert-base-uncased',
                                                      num_labels = 2,
                                                      output_attentions = False,
                                                      output_hidden_states = False)

Some weights of the model checkpoint at bert-base-uncased were not used when initializing BertForSequenceClassification: ['cls.predictions.decoder.weight', 'cls.predictions.transform.LayerNorm.weight', 'cls.seq_relationship.bias', 'cls.predictions.transform.dense.bias', 'cls.seq_relationship.weight', 'cls.predictions.transform.LayerNorm.bias', 'cls.predictions.transform.dense.weight', 'cls.predictions.bias']
- This IS expected if you are initializing BertForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertForSequenceClassification were not initialized from the model checkpoint at

In [68]:
model.load_state_dict(torch.load(f'Models/ BERT_ft_epoch3.model'))

<All keys matched successfully>

In [69]:
len(dataloader_test)

465

In [23]:
val_loss, predictions, true_vals = evaluate(dataloader_val,model)

100%|██████████| 10000/10000 [42:00<00:00,  3.97it/s]


In [24]:
print(val_loss)

0.27637956384159623


In [28]:
val_loss, predictions, true_vals = evaluate(dataloader_val,model)

100%|██████████| 10000/10000 [41:56<00:00,  3.97it/s]


In [29]:
print(val_loss)

0.2892338718647137


In [70]:
val_loss, predictions, true_vals = evaluate(dataloader_test,model)

100%|██████████| 465/465 [01:06<00:00,  7.01it/s]


In [ ]:
val_f1 = f1_score_func(predictions, true_vals)
print("F1 score is:",val_f1)

In [72]:
accuracy_per_class(predictions, true_vals) # For epoch 3

Class: Negative
Accuracy:3310/4347

Class: Positive
Accuracy:8786/10533

Total accuracy is : 0.8129032258064516



In [ ]:
train_loss = []
val_loss_total = []
for epoch in tqdm(range(3, epochs+1)):
    
    model.cuda()
    model.train()
    
    loss_train_total = 0
    
    progress_bar = tqdm(dataloader_train, 
                        desc = 'Epoch {:1d}'.format(epoch), 
                        leave = False, 
                        disable = False)
    counter = 0
    for batch in progress_bar:
        
        model.zero_grad() #set gradient to 0
        batch = tuple(b.cuda() for b in batch)
        
        inputs = {'input_ids': batch[0], 
                  'attention_mask': batch[1], 
                  'labels': batch[2]}        
        outputs = model(**inputs) #unpack the dict straight into inputs
        
        loss = outputs[0]
        loss_train_total += loss.item()
        loss.backward()
        
        torch.nn.utils.clip_grad_norm_(model.parameters(), 1.0)
        
        optimizer.step()
        scheduler.step()
        counter += 1
#         if counter%2000 == 0:
#             print("Epoch: {}/{}...".format(epoch, epochs),
#                     "Step: {}...".format(counter),
#                     "Loss: {}...".format(loss.item()))
        progress_bar.set_postfix({'training_loss': '{:.3f}'.format(loss.item() / len(batch))})
        
    torch.save(model.state_dict(), f'Models/ BERT_ft_epoch{epoch}.model')
    
    tqdm.write('\n Epoch {epoch}')
    
    loss_train_ave = loss_train_total / len(dataloader_train)
    train_loss.append(loss_train_ave)
    tqdm.write('Training loss: {loss_train_avg}')
    
    val_loss, predictions, true_vals = evaluate(dataloader_val,model)
    val_loss_total.append(val_loss)
    val_f1 = f1_score_func(predictions, true_vals)
    tqdm.write(f'Validation loss: {val_loss}')
    tqdm.write(f'F1 Score (weighted): {val_f1}')
    accuracy_per_class(predictions, true_vals)

Epoch 3:   0%|          | 94/40000 [01:17<9:01:35,  1.23it/s, training_loss=0.044]


Epoch 3:   0%|          | 188/40000 [02:34<9:00:29,  1.23it/s, training_loss=0.095]


Epoch 3:   1%|          | 282/40000 [03:50<8:59:11,  1.23it/s, training_loss=0.081]


Epoch 3:   1%|          | 376/40000 [05:06<8:58:00,  1.23it/s, training_loss=0.042]


Epoch 3:   1%|          | 470/40000 [06:23<8:56:20,  1.23it/s, training_loss=0.064]


...

Epoch 3:  46%|████▌     | 18394/40000 [4:09:57<4:53:45,  1.23it/s, training_loss=0.064]


Epoch 3:  46%|████▌     | 18484/40000 [4:11:10<4:52:39,  1.23it/s, training_loss=0.035]


Epoch 3:  46%|████▋     | 18574/40000 [4:12:24<4:51:48,  1.22it/s, training_loss=0.067]


Epoch 3:  47%|████▋     | 18664/40000 [4:13:37<4:50:22,  1.22it/s, training_loss=0.082]


Epoch 3:  47%|████▋     | 18722/40000 [4:14:25<4:49:58,  1.22it/s, training_loss=0.101]

In [15]:
print(device)

cuda:0


In [18]:
torch.cuda.memory_allocated(device=device)

0